# Requires TF2
https://github.com/eleozzr/desc/blob/master/desc_2.1.1_paul.ipynb

In [1]:
# !pip install desc

     |████████████████████████████████| 5.2MB 5.4MB/s eta 0:00:01
     |████████████████████████████████| 394.3MB 92kB/s  eta 0:00:012   |█                               | 11.4MB 6.6MB/s eta 0:00:58�██████████          | 270.3MB 7.5MB/s eta 0:00:17
     |████████████████████████████████| 71kB 9.9MB/s  eta 0:00:01
     |████████████████████████████████| 471kB 10.8MB/s eta 0:00:01
     |████████████████████████████████| 10.6MB 7.6MB/s eta 0:00:01
     |████████████████████████████████| 133kB 10.8MB/s eta 0:00:01
     |████████████████████████████████| 3.8MB 10.4MB/s eta 0:00:01
     |████████████████████████████████| 122kB 10.5MB/s eta 0:00:01


     |████████████████████████████████| 788kB 9.0MB/s eta 0:00:01
     |████████████████████████████████| 163kB 10.8MB/s eta 0:00:01
     |████████████████████████████████| 81kB 10.2MB/s eta 0:00:01
     |████████████████████████████████| 153kB 11.0MB/s eta 0:00:01
ERROR: tensorflow-gpu 1.15.0 has requirement gast==0.2.2, but you'll have gast 0.3.3 which is incompatible.
ERROR: tensorflow-gpu 1.15.0 has requirement tensorboard<1.16.0,>=1.15.0, but you'll have tensorboard 2.4.1 which is incompatible.
ERROR: tensorflow-gpu 1.15.0 has requirement tensorflow-estimator==1.15.1, but you'll have tensorflow-estimator 2.4.0 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement numpy~=1.19.2, but you'll have numpy 1.17.4 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement six~=1.15.0, but you'll have six 1.12.0 which is incompatible.
  Found existing installation: opt-einsum 3.2.1
    Uninstalling opt-einsum-3.2.1:
      Successfully uninstalled opt-einsum-3.2.1
  Found exist

In [2]:
import desc  

In [4]:
import sys
sys.path.append("..")
# import gnn_utils

import matplotlib.pyplot as plt
from scziDesk_preprocess import *
from scziDesk_network import *
from scziDesk_utils import *
import argparse
from sklearn.metrics import adjusted_rand_score, normalized_mutual_info_score,silhouette_score
from collections import Counter
import glob2
import tensorflow as tf
import time
import desc  
plt.ion()
plt.show()
%load_ext autoreload
%autoreload 2
print(desc.__version__, tf.__version__)

2.1.1 2.4.1


/opt/conda/lib/python3.7/site-packages/scanpy/api/__init__.py:7: FutureWarning: 

In a future version of Scanpy, `scanpy.api` will be removed.
Simply use `import scanpy as sc` and `import scanpy.external as sce` instead.

  FutureWarning,
Using TensorFlow backend.


In [5]:
for category in [ "real_data"#, "balanced_data", "imbalanced_data"
                ]:

    path= ".."
    if category in ["balanced_data", "imbalanced_data"]:
        files = glob2.glob(f'{path}/R/simulated_data/{category}/*.h5')
        files = [f[len(f"{path}/R/simulated_data/{category}/"):-3] for f in files]
    else:
        files = glob2.glob(f'{path}/real_data/*.h5')
        files = [f[len(f"{path}/real_data/"):-3] for f in files]
    print(files)

    df = pd.DataFrame(columns = ["dataset", "ARI", "NMI", "sil", "run", "time", "pred"])
    for dataset in files:
        if category in ["balanced_data", "imbalanced_data"]:
            data_mat = h5py.File(f"{path}/R/simulated_data/{category}/{dataset}.h5","r")
        else:
            data_mat = h5py.File(f"{path}/real_data/{dataset}.h5","r")

        Y = np.array(data_mat['Y'])
        X = np.array(data_mat['X'])
        print(f">>>>dataset {dataset}")
        if X.shape[0] > 10000:
            continue

        X = np.ceil(X).astype(np.int)
        for run in range(3):
            start = time.time()
            seed = run
            np.random.seed(seed)
    #         tf.reset_default_graph()
            save_dir="desc"
            adata = sc.AnnData(X)
            adata.obs['Group'] = Y
            sc.pp.log1p(adata)
            sc.pp.highly_variable_genes(adata,n_top_genes=1000,subset=True,inplace=True)

            sc.pp.scale(adata,max_value=6)
            adata=desc.train(adata,
                    dims=[adata.shape[1],64,32],
                    tol=0.005,
                    n_neighbors=10,
                    batch_size=256,
                    louvain_resolution=[1.0],# not necessarily a list, you can only set one value, like, louvain_resolution=1.0
                    save_dir=str(save_dir),
                    do_tsne=True,
                    learning_rate=200, # the parameter of tsne
                    use_GPU=True,
                    num_Cores=1, #for reproducible, only use 1 cpu
                    num_Cores_tsne=4,
                    save_encoder_weights=False,
                    save_encoder_step=3,# save_encoder_weights is False, this parameter is not used
                    use_ae_weights=False,
                    do_umap=False)
            elapsed = time.time() - start
            truth = adata.obs["Group"]
            pred = adata.obs["desc_1.0"]
            ARI = np.around(adjusted_rand_score(truth, pred), 5)
            NMI = np.around(normalized_mutual_info_score(truth, pred), 5)
            ss = silhouette_score(adata.X, pred)

            df.loc[df.shape[0]] = [dataset, ARI, NMI, ss, run, elapsed, pred]
            df.to_pickle(f"../output/pickle_results/{category}/{category}_desc.pkl")

['Quake_Smart-seq2_Trachea', 'Quake_Smart-seq2_Diaphragm', 'Quake_10x_Spleen', 'Young', '10X_PBMC_select_2100', 'mouse_ES_cell', 'Adam', 'Quake_10x_Bladder', 'Quake_Smart-seq2_Lung', 'worm_neuron_cell_select_2100', 'Quake_10x_Limb_Muscle', 'worm_neuron_cell', 'mouse_bladder_cell', 'mouse_ES_cell_select_2100', 'Romanov', 'Quake_Smart-seq2_Limb_Muscle', 'Muraro', 'mouse_bladder_cell_select_2100', '10X_PBMC']
>>>>dataset Quake_Smart-seq2_Trachea
Start to process resolution= 1.0
The number of cpu in your computer is 12

('Failed to import pydot. You must `pip install pydot` and install graphviz (https://graphviz.gitlab.io/download/), ', 'for `pydotprint` to work.')
use_ae_weights=False, the program will rerun autoencoder
Pretraining the 1th layer...
learning rate = 0.1
Epoch 1/50
6/6 [==============================] - 0s 6ms/step - loss: 0.7667
Epoch 2/50
6/6 [==============================] - 0s 5ms/step - loss: 0.7545
Epoch 3/50
6/6 [==============================] - 0s 6ms/step - loss: 

6/6 [==============================] - 0s 4ms/step - loss: 0.5137
Epoch 18/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5096
Epoch 19/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4966
Epoch 20/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5179
Epoch 21/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5030
Epoch 22/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5132
Epoch 23/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5157
Epoch 24/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5144
Epoch 25/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4996
Epoch 26/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5058
Epoch 27/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5123
Epoch 28/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5061
Epoch 29/50
6/6 [==============================] - 0s 4ms/step - loss: 0.508

6/6 [==============================] - 0s 5ms/step - loss: 0.7022
Epoch 8/50
6/6 [==============================] - 0s 6ms/step - loss: 0.6926
Epoch 9/50
6/6 [==============================] - 0s 6ms/step - loss: 0.6799
Epoch 10/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6732
Epoch 11/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6585
Epoch 12/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6652
Epoch 13/50
6/6 [==============================] - 0s 6ms/step - loss: 0.6678
Epoch 14/50
6/6 [==============================] - 0s 6ms/step - loss: 0.6627
Epoch 15/50
6/6 [==============================] - 0s 6ms/step - loss: 0.6536
Epoch 16/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6409
Epoch 17/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6354
Epoch 18/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6277
Epoch 19/50
6/6 [==============================] - 0s 5ms/step - loss: 0.6085


6/6 [==============================] - 0s 4ms/step - loss: 0.4972
Epoch 37/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4969
Epoch 38/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5005
Epoch 39/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4912
Epoch 40/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5021
Epoch 41/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5044
Epoch 42/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4955
Epoch 43/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4954
Epoch 44/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5013
Epoch 45/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5026
Epoch 46/50
6/6 [==============================] - 0s 4ms/step - loss: 0.5017
Epoch 47/50
6/6 [==============================] - 0s 4ms/step - loss: 0.4988
Epoch 48/50
6/6 [==============================] - 0s 4ms/step - loss: 0.489

6/6 [==============================] - 0s 6ms/step - loss: 0.6029
Epoch 27/50
6/6 [==============================] - 0s 6ms/step - loss: 0.6079
Epoch 28/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5998
Epoch 29/50
6/6 [==============================] - 0s 6ms/step - loss: 0.5995
Epoch 30/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5853
Epoch 31/50
6/6 [==============================] - 0s 6ms/step - loss: 0.5851
Epoch 32/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5864
Epoch 33/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5897
Epoch 34/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5869
Epoch 35/50
6/6 [==============================] - 0s 6ms/step - loss: 0.5747
Epoch 36/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5787
Epoch 37/50
6/6 [==============================] - 0s 5ms/step - loss: 0.5758
Epoch 38/50
6/6 [==============================] - 0s 5ms/step - loss: 0.578

...

12/12 [==============================] - 0s 2ms/step - loss: 0.1000
The value of delta_label of current 57 th iteration is 0.007 >= tol 0.005
Epoch 1/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1081
Epoch 2/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1063
Epoch 3/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1045
Epoch 4/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1028
Epoch 5/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1012
The value of delta_label of current 58 th iteration is 0.006333333333333333 >= tol 0.005
Epoch 1/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1106
Epoch 2/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1085
Epoch 3/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1063
Epoch 4/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1043
Epoch 5/5
12/12 [==============================] - 0s 2ms/step - lo

12/12 [==============================] - 0s 6ms/step - loss: 0.9153
Epoch 5/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9169
Epoch 6/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9109
Epoch 7/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9162
Epoch 8/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9125
Epoch 9/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9121
Epoch 10/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9120
Epoch 11/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9166
Epoch 12/50
12/12 [==============================] - 0s 6ms/step - loss: 0.9145
Epoch 13/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9154
Epoch 14/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9149
Epoch 15/50
12/12 [==============================] - 0s 5ms/step - loss: 0.9148
Epoch 16/50
12/12 [==============================] - 0s 5

12/12 [==============================] - 0s 4ms/step - loss: 0.8642
Epoch 10/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8641
Epoch 11/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8680
Epoch 00011: early stopping
learning rate = 0.001
Epoch 1/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8640
Epoch 2/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8640
Epoch 3/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8656
Epoch 4/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8667
Epoch 5/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8687
Epoch 6/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8635
Epoch 7/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8678
Epoch 8/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8645
Epoch 9/50
12/12 [==============================] - 0s 4ms/step - loss: 0.8642
Epoch 10/50

12/12 [==============================] - 0s 2ms/step - loss: 0.0330
Epoch 4/5
12/12 [==============================] - 0s 2ms/step - loss: 0.0323
Epoch 5/5
12/12 [==============================] - 0s 3ms/step - loss: 0.0316
The value of delta_label of current 29 th iteration is 0.016666666666666666 >= tol 0.005
Epoch 1/5
12/12 [==============================] - 0s 2ms/step - loss: 0.0375
Epoch 2/5
12/12 [==============================] - 0s 2ms/step - loss: 0.0366
Epoch 3/5
12/12 [==============================] - 0s 2ms/step - loss: 0.0358
Epoch 4/5
12/12 [==============================] - 0s 2ms/step - loss: 0.0349
Epoch 5/5
12/12 [==============================] - 0s 3ms/step - loss: 0.0341
The value of delta_label of current 30 th iteration is 0.015 >= tol 0.005
Epoch 1/5
12/12 [==============================] - 0s 3ms/step - loss: 0.0409
Epoch 2/5
12/12 [==============================] - 0s 3ms/step - loss: 0.0398
Epoch 3/5
12/12 [==============================] - 0s 2ms/step - lo

12/12 [==============================] - 0s 2ms/step - loss: 0.1092
The value of delta_label of current 63 th iteration is 0.010333333333333333 >= tol 0.005
Epoch 1/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1234
Epoch 2/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1202
Epoch 3/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1174
Epoch 4/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1149
Epoch 5/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1127
The value of delta_label of current 64 th iteration is 0.006666666666666667 >= tol 0.005
Epoch 1/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1245
Epoch 2/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1221
Epoch 3/5
12/12 [==============================] - 0s 3ms/step - loss: 0.1200
Epoch 4/5
12/12 [==============================] - 0s 2ms/step - loss: 0.1181
Epoch 5/5
12/12 [==============================] - 0

In [ ]:
df.groupby("dataset").mean()